In [2]:
import logging
logging.getLogger('tensorflow').disabled = True
from sklearn.model_selection import train_test_split
import pandas as pd
import tensorflow as tf
import tensorflow_hub as hub
from datetime import datetime

C:\Users\Maryia_Ivanina\AppData\Local\Continuum\anaconda3\envs\cornell\lib\site-packages\tensorflow\python\framework\dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\Maryia_Ivanina\AppData\Local\Continuum\anaconda3\envs\cornell\lib\site-packages\tensorflow\python\framework\dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\Maryia_Ivanina\AppData\Local\Continuum\anaconda3\envs\cornell\lib\site-packages\tensorflow\python\framework\dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.d

In [2]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [5]:
!pip install bert-tensorflow

    100% |████████████████████████████████| 71kB 1.2MB/s ta 0:00:011


In [3]:
import bert
from bert import run_classifier
from bert import optimization
from bert import tokenization

In [4]:
import pandas as pd
import requests
import json
import re
import sys
import numpy as np
import os
import nltk
import pickle

sys.path.append('../src')

from commons import elastic
from langdetect import detect
from text_processing import text_normalizer
from importlib import reload
from text_processing import duplicate_finder
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.wordnet import WordNetLemmatizer
import spacy
import Levenshtein
text_normalizer = reload(text_normalizer)
from dateutil.parser import parse
from utilities import excel_writer, excel_reader
from sklearn.model_selection import train_test_split

def get_train_and_test_data_splitted(temp_df, all_dataset = False, test_size=0.05):
    if all_dataset:
        train_data = temp_df
        test_data = temp_df
    else:
        train_data_x, test_data_x,train_y,test_y = train_test_split([data[:-1] for data in temp_df.values], [data[-1] for data in temp_df.values], test_size=test_size)
        train_data = np.concatenate((train_data_x,[[val]for val in train_y]),axis=1)
        test_data = np.concatenate((test_data_x,[[val] for val in test_y]),axis=1)
    return pd.DataFrame(train_data, columns=temp_df.columns), pd.DataFrame(test_data, columns=temp_df.columns)

C:\Users\Maryia_Ivanina\AppData\Local\Continuum\anaconda3\envs\cornell\lib\site-packages\gensim\utils.py:1209: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [5]:
!pip install scikit-multilearn==0.2.0

    100% |████████████████████████████████| 92kB 1.3MB/s ta 0:00:011


# Data

In [4]:
all_data = []
y = []
outcomes_data_folder = "../tmp/outcomes_data"
for file in os.listdir(outcomes_data_folder):
    df_outcome_mary = excel_reader.ExcelReader().read_df_from_excel(os.path.join(outcomes_data_folder, file))
    for i in range(len(df_outcome_mary)):
        outcomes = []
        outcomes_per_label = []
        outcomes_labels = []
        for column in ['Soil health', 'Fertilizer use', 'Water use', 'Gender',
           'Greenhouse gas emissions', 'Livelihood', 'Market access', 'Nutrition',
           'Production', 'Resilience', 'Knowledge sharing', 'Practice change',
           'Social inclusion', 'Poverty reduction', 'Environment impact']:
            outcomes_found = set([outcome for outcome in df_outcome_mary[column].values[i].split(";") if outcome.strip()])
            outcomes.extend(outcomes_found)
            for outcome in outcomes_found:
                outcomes_per_label.append((outcome, column))
            
            outcomes_labels.append(1 if len(outcomes_found) else 0)
        y.append(outcomes_labels)
        outcomes_found = set()
        for sent in nltk.sent_tokenize(df_outcome_mary["Sentence"].values[i]):
            found_entities = []
            found_outcome_plus_labels = []
            for outcome, label in outcomes_per_label:
                outcome = outcome.strip().strip(",").strip(".").strip()
                if outcome.lower() in sent.lower():
                    start_ind = sent.lower().rfind(outcome.lower())
                    end_ind = start_ind + len(outcome)
                    if sent[start_ind: end_ind].lower() != outcome.lower():
                        print(sent)
                        print(start_ind, end_ind)
                        print(sent[start_ind: end_ind])
                        print(sent[start_ind: end_ind].lower(), outcome.lower())
                    found_entities.append((start_ind, end_ind, 'OUTCOME'))
                    outcomes_found.add(outcome)
                    found_outcome_plus_labels.append((outcome, label))
            all_data.append((sent, {'entities': found_entities}, found_outcome_plus_labels))
        if len(outcomes_found) != len(set(outcomes)):
            print(outcomes, outcomes_found)
            print(i)
print("All data ", len(all_data))

All data  2622


In [5]:
from skmultilearn.model_selection import iterative_train_test_split
from skmultilearn.model_selection.measures import get_combination_wise_output_matrix
X_train, y_train, X_test, y_test = iterative_train_test_split(np.asarray(all_data), np.asarray(y), test_size = 0.1)

In [6]:
def split_outcomes_data(merged_data):
    train_data = []
    train_data_outcomes = []
    train_sentences = []
    for data in merged_data:
        train_data.append((data[0], data[1]))
        train_data_outcomes.extend(data[2])
        train_sentences.append((data[0], [d[1] for d in data[2]]))
    return train_data, train_data_outcomes, train_sentences
        

TRAIN_DATA, outcomes_train_label_data, outcomes_sentences_train_data = split_outcomes_data(X_train)
EVAL_DATA, outcomes_eval_label_data, outcomes_sentences_eval_data = split_outcomes_data(X_test)
print("Train data", len(TRAIN_DATA))
print("Test data", len(EVAL_DATA))

Train data 2359
Test data 263


In [6]:
import pickle
from sklearn.utils import shuffle
TRAIN_DATA, outcomes_train_label_data, outcomes_sentences_train_data, EVAL_DATA, outcomes_eval_label_data, outcomes_sentences_eval_data = pickle.load(open("/hdd2/data/maryia_pavlovets/entity-recognition-model-more-2610_train_data", "rb"))
TRAIN_DATA = shuffle(TRAIN_DATA)
outcomes_train_label_data = shuffle(outcomes_train_label_data)
outcomes_sentences_train_data = shuffle(outcomes_sentences_train_data)

In [7]:
pd.DataFrame(outcomes_train_label_data, columns=["Text", "Label"])["Label"].value_counts()

Livelihood                  463
Production                  405
Greenhouse gas emissions    232
Market access               222
Nutrition                   208
Resilience                  198
Soil health                 179
Practice change             157
Gender                      147
Fertilizer use              128
Water use                   128
Knowledge sharing           125
Environment impact          117
Social inclusion            106
Poverty reduction           103
Name: Label, dtype: int64

In [8]:
pd.DataFrame(outcomes_eval_label_data, columns=["Text", "Label"])["Label"].value_counts()

Livelihood                  45
Production                  44
Nutrition                   26
Greenhouse gas emissions    24
Resilience                  22
Soil health                 21
Market access               21
Practice change             18
Gender                      16
Fertilizer use              14
Knowledge sharing           14
Social inclusion            13
Water use                   13
Environment impact          13
Poverty reduction           12
Name: Label, dtype: int64

In [4]:
def highlight_max(data, color='yellow'):
    '''
    highlight the maximum in a Series or DataFrame
    '''
    attr = 'background-color: {}'.format(color)
    #remove % and cast to float
    if data.ndim == 1:  # Series from .apply(axis=0) or axis=1
        is_max = data == data.max()
        return [attr if v else '' for v in is_max]
    else:  # from .apply(axis=None)
        print(data.max())
        is_max = data == data.max().max()
        return pd.DataFrame(np.where(is_max, attr, ''),
                            index=data.index, columns=data.columns)

In [4]:
from outcomes_modelling import outcomes_full_logic_labeller
outcomes_full_logic_labeller = reload(outcomes_full_logic_labeller)
_outcomes_full_logic_labeller = outcomes_full_logic_labeller.OutcomesFullLogicLabeller(
    "/hdd2/data/maryia_pavlovets/bert_exp_outcome_new",
    "/hdd2/data/maryia_pavlovets/entity-recognition-model-more-2610")
_outcomes_full_logic_labeller.train_model("/hdd2/data/maryia_pavlovets/entity-recognition-model-more-2610_train_data")

Train data distribution
Livelihood                  463
Production                  405
Greenhouse gas emissions    232
Market access               222
Nutrition                   208
Resilience                  198
Soil health                 179
Practice change             157
Gender                      147
Water use                   128
Fertilizer use              128
Knowledge sharing           125
Environment impact          117
Social inclusion            106
Poverty reduction           103
Name: Label, dtype: int64
Valid data distribution
Livelihood                  45
Production                  44
Nutrition                   26
Greenhouse gas emissions    24
Resilience                  22
Market access               21
Soil health                 21
Practice change             18
Gender                      16
Knowledge sharing           14
Fertilizer use              14
Water use                   13
Social inclusion            13
Environment impact          13
Poverty redu

KeyboardInterrupt: 

In [7]:
_outcomes_full_logic_labeller.print_statistics()

Mean the best F1 score:  0.8390244371736914


In [8]:
_outcomes_full_logic_labeller.save_model()

In [13]:
def predict_proba(doc):
    return np.asarray(_outcomes_sentence_labeler.predict_for_df(pd.DataFrame([(d, -1) for d in doc], columns=["text", "label"]))[0])

In [98]:
idx = 149
text = outcomes_sentences_eval_data[idx][0]
print(text)
print(outcomes_sentences_eval_data[idx][1])

LCA results indicate that it is possible to reduce the GWP associated with refrigerated transportation by increasing local fish production and decreasing importation, especially given the available water potential of Bahia.
['Greenhouse gas emissions', 'Market access', 'Production']


In [10]:
[(t[0], idx) for idx,t in enumerate(outcomes_sentences_eval_data) if "Market access" in t[1]]

[('Immediately prior to, and during the early stages of the 1939-1945 war central and western Europe were producing more than ever before, but at present they are largely dependent upon imports.',
  5),
 ('Urbanizing food markets As developing countries are undergoing a dietary transition as a result of urbanization, consumers face a new slate of potential health benefits and health risks.',
  15),
 ('In the first experiment, i reduce the marginal costs of traders in randomly selected markets by offering to traders a subsidy per bag sold.',
  17),
 ('In the face of the world market price increases of the recent past, we analyze the regional marketing chain of this commodity qualitatively and econometrically investigating to what extent smallholder farmers in developing countries are affected by international price movements.',
  21),
 ('Improving the quality of rural roads reduces the cost of arranging transactions between spatially separate locations and can significantly affect agric

In [99]:
from outcomes_modelling import outcomes_sentence_labeler
import eli5
from eli5.lime import TextExplainer

label = "Market access"
_outcomes_sentence_labeler = outcomes_sentence_labeler.OutcomesSentenceLabeler(
        "/hdd2/data/maryia_pavlovets/bert_exp_outcome/outcomes_12.12_%s_4"%label, gpu_device_num=0)
te = TextExplainer(random_state=42)
te.fit(text, predict_proba)
te.show_prediction(targets=[1])

Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0


In [5]:
from outcomes_modelling import outcomes_full_logic_labeller
outcomes_full_logic_labeller = reload(outcomes_full_logic_labeller)
_outcomes_full_logic_labeller = outcomes_full_logic_labeller.OutcomesFullLogicLabeller(
    "/hdd2/data/maryia_pavlovets/bert_exp_outcome_new",
    "/hdd2/data/maryia_pavlovets/entity-recognition-model-more-2610")

In [6]:
from time import time
for folder in ["processed_usaid_pdfs"]: #["subset_usaid", "dfs_data","teams_dataset","big_dataset_1"]:
    for filename in os.listdir(os.path.join("../tmp", folder)):
        print(folder, filename)
        new_folder = (folder+"_new") if folder in ["big_dataset_1", "processed_usaid_pdfs"] else folder
        print(new_folder)
        if folder != new_folder and os.path.exists(os.path.join("../tmp", new_folder, filename)):
            print("Already processed")
            continue
        start = time()
        df = excel_reader.ExcelReader().read_df_from_excel(os.path.join("../tmp", folder, filename))
        print(len(df))
        df["text"] = df["sentence"] #df["title"] + " . " + df["abstract"]
        found_labels, outcome_details = _outcomes_full_logic_labeller.predict_all_labels(df["text"].values)
        df["outcomes_found"] = found_labels
        df["outcomes_details"] = ["\n".join(detail) for detail in outcome_details]
        df = df.drop(["text"], axis=1)
        print("Finished ", (time() - start))
        os.makedirs(os.path.join("../tmp", new_folder), exist_ok=True)
        excel_writer.ExcelWriter().save_df_in_excel(df, os.path.join("../tmp", new_folder, filename))

processed_usaid_pdfs PA00KNS3.xlsx
processed_usaid_pdfs_new
Read file ../tmp/processed_usaid_pdfs/PA00KNS3.xlsx: 0.12s
Processed file ../tmp/processed_usaid_pdfs/PA00KNS3.xlsx: 0.01s
430
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer load

Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used

Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded


Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Finished  106.01663994789124
Saving...
Saved to ../tmp/processed_usaid_pdfs

Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Finished  183.9133129119873
Saving...
Saved to ../tmp/processed_usaid_pdfs_new/PA00KC72.xlsx
processed_usaid_pdfs PA00SV1V.xlsx
processed_usaid_pdfs_new
Read file ../tmp/processed_usaid_pdfs/PA00SV1V.xlsx: 0.05s
Processed file ../tmp/processed_usaid_pdfs/PA00SV1V.xlsx: 0.05s
1625
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer lo

...

Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded


Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Finished  127.33465528488159
Saving...
Saved to ../tmp/processed_usaid_pdfs_new/PDACT321.xlsx
processed_usaid_pdfs PA00JWVB.xlsx
processed_usaid_pdfs_new
Read file ../tmp/processed_usaid_p

Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Finished  114.60183548927307
Saving...
Saved to ../tmp/processed_usaid_pdfs_new/PA00JX5R.xlsx
processed_usaid_pdfs PA00HWHP.xlsx
processed_usaid_pdfs_new
Read file ../tmp/processed_usaid_pdfs/PA00HWHP.xlsx: 0.01s
Processed file ../tmp/processed_usaid_pdfs/PA00HWHP.xlsx: 0.00s
107
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
C

Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Finished  147.9279363155365
Saving...
Saved to ../tmp/processed_usaid_pdfs_new/PA00KMCM.xlsx
processed_usaid_pdfs PA00KNFC.xlsx
processed_usaid_pdfs_new
Read file ../tmp/processed_usaid_pdfs/PA00KNFC.xlsx: 0.01s
Processed file ../tmp/processed_usaid_pdfs/PA00KNFC.xlsx: 0.01s
416
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model

Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Finished  121.95890045166016
Saving...
Saved to ../tmp/processed_usaid_pdfs_new/PA00T931.xlsx
processed_usaid_pdfs AID-623-BC-11-00001.xlsx
processed_usaid_pdfs_new
Read file ../tmp/processed_usaid_pdfs/AID-623-BC-11-00001.xlsx: 0.01s
Processed file ../tmp/processed_usaid_pdfs/AID-623-BC-11-00001.xlsx: 0.01s
232
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Used for model gpu 0
Started tokenizer loading
Used gpu 0
Model pa

In [300]:
from outcomes_modelling import outcomes_extracted_labeler
outcomes_extracted_labeler = reload(outcomes_extracted_labeler)

_outcomes_extracted_labeler = outcomes_extracted_labeler.OutcomesExtractedLabeler("outcomes_new_%s_1"%label_to_train, gpu_device_num=0)

Started tokenizer loading
Used gpu 0
INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I1106 14:17:18.598217 139697590273856 saver.py:1483] Saver not created because there are no variables in the graph to restore


Model partly loaded
Tokenizrer loaded
0
INFO:tensorflow:Using config: {'_model_dir': 'outcomes_new_Livelihood_1', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f0d0481cfd0>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


I1106 14:17:18.949852 139697590273856 estimator.py:201] Using config: {'_model_dir': 'outcomes_new_Livelihood_1', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f0d0481cfd0>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Config is done


In [333]:
train_data_df = _outcomes_extracted_labeler.prepare_data_df(outcomes_train_label_data, label_to_train)
test_data_df =  _outcomes_extracted_labeler.prepare_data_df(outcomes_eval_label_data, label_to_train)

In [303]:
res = _outcomes_extracted_labeler.train_model(train_data_df, test_data_df)

INFO:tensorflow:Writing example 0 of 945


I1106 14:19:09.753513 139697590273856 base_bert_model.py:424] Writing example 0 of 945


INFO:tensorflow:*** Example ***


I1106 14:19:09.755489 139697590273856 base_bert_model.py:400] *** Example ***


INFO:tensorflow:guid: None


...

I1106 14:23:03.876618 139697590273856 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I1106 14:23:03.949216 139697590273856 session_manager.py:493] Done running local_init_op.


[[79  3]
 [ 5 18]]
              precision    recall  f1-score   support

           0       0.94      0.96      0.95        82
           1       0.86      0.78      0.82        23

   micro avg       0.92      0.92      0.92       105
   macro avg       0.90      0.87      0.88       105
weighted avg       0.92      0.92      0.92       105

F1 score:  0.8849945235487404


([array([0.03499742, 0.96500254], dtype=float32),
  array([0.04313593, 0.95686406], dtype=float32),
  array([0.9787573 , 0.02124265], dtype=float32),
  array([0.03718882, 0.9628112 ], dtype=float32),
  array([0.03236588, 0.96763414], dtype=float32),
  array([0.9613243 , 0.03867568], dtype=float32),
  array([0.0382337 , 0.96176624], dtype=float32),
  array([0.29467875, 0.7053212 ], dtype=float32),
  array([0.11849163, 0.88150835], dtype=float32),
  array([0.4911228 , 0.50887716], dtype=float32),
  array([0.9951497 , 0.00485033], dtype=float32),
  array([0.98830754, 0.01169246], dtype=float32),
  array([0.99258703, 0.00741296], dtype=float32),
  array([0.9928559 , 0.00714407], dtype=float32),
  array([0.99517435, 0.00482567], dtype=float32),
  array([0.98014414, 0.01985588], dtype=float32),
  array([0.99473333, 0.00526668], dtype=float32),
  array([0.9937966 , 0.00620346], dtype=float32),
  array([0.96614265, 0.03385735], dtype=float32),
  array([0.97086203, 0.02913793], dtype=float32),


In [325]:
from outcomes_modelling import outcomes_sentence_labeler
outcomes_sentence_labeler = reload(outcomes_sentence_labeler)
_outcomes_sentence_labeler = outcomes_sentence_labeler.OutcomesSentenceLabeler("outcomes_new_%s_3"%label_to_train, gpu_device_num=0)

Started tokenizer loading
Used gpu 0
INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I1106 14:52:32.563433 139697590273856 saver.py:1483] Saver not created because there are no variables in the graph to restore


Model partly loaded
Tokenizrer loaded
0
INFO:tensorflow:Using config: {'_model_dir': 'outcomes_new_Livelihood_3', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f0c2d62c048>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


I1106 14:52:32.915181 139697590273856 estimator.py:201] Using config: {'_model_dir': 'outcomes_new_Livelihood_3', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f0c2d62c048>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Config is done


In [326]:
train_data_df = _outcomes_sentence_labeler.prepare_df_data_sentences(outcomes_sentences_train_data, label_to_train, include_empty_sentences=False)
test_data_df = _outcomes_sentence_labeler.prepare_df_data_sentences(outcomes_sentences_eval_data, label_to_train, include_empty_sentences=True)

In [327]:
res = _outcomes_sentence_labeler.train_model(train_data_df, test_data_df)

INFO:tensorflow:Writing example 0 of 729


I1106 14:53:00.227456 139697590273856 base_bert_model.py:424] Writing example 0 of 729


INFO:tensorflow:*** Example ***


I1106 14:53:00.229801 139697590273856 base_bert_model.py:400] *** Example ***


INFO:tensorflow:guid: None


...

INFO:tensorflow:Running local_init_op.


I1106 14:56:08.942626 139697590273856 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I1106 14:56:09.018362 139697590273856 session_manager.py:493] Done running local_init_op.


[[120  11]
 [  6  14]]
              precision    recall  f1-score   support

           0       0.95      0.92      0.93       131
           1       0.56      0.70      0.62        20

   micro avg       0.89      0.89      0.89       151
   macro avg       0.76      0.81      0.78       151
weighted avg       0.90      0.89      0.89       151

F1 score:  0.7780371811500216


In [328]:
from outcomes_modelling import outcomes_sentence_labeler
outcomes_sentence_labeler = reload(outcomes_sentence_labeler)
_outcomes_sentence_labeler = outcomes_sentence_labeler.OutcomesSentenceLabeler("outcomes_new_%s_4"%label_to_train, gpu_device_num=0)

Started tokenizer loading
Used gpu 0
INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I1106 14:56:33.299341 139697590273856 saver.py:1483] Saver not created because there are no variables in the graph to restore


Model partly loaded
Tokenizrer loaded
0
INFO:tensorflow:Using config: {'_model_dir': 'outcomes_new_Livelihood_4', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f0c2c2de400>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


I1106 14:56:33.661720 139697590273856 estimator.py:201] Using config: {'_model_dir': 'outcomes_new_Livelihood_4', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f0c2c2de400>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Config is done


In [329]:
train_data_df = _outcomes_sentence_labeler.prepare_df_data_sentences(outcomes_sentences_train_data, label_to_train, include_empty_sentences=True)
test_data_df = _outcomes_sentence_labeler.prepare_df_data_sentences(outcomes_sentences_eval_data, label_to_train, include_empty_sentences=True)

In [330]:
res = _outcomes_sentence_labeler.train_model(train_data_df, test_data_df)

INFO:tensorflow:Writing example 0 of 1674


I1106 14:56:49.445896 139697590273856 base_bert_model.py:424] Writing example 0 of 1674


INFO:tensorflow:*** Example ***


I1106 14:56:49.447578 139697590273856 base_bert_model.py:400] *** Example ***


INFO:tensorflow:guid: None


...

INFO:tensorflow:Running local_init_op.


I1106 15:03:26.891546 139697590273856 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I1106 15:03:26.961287 139697590273856 session_manager.py:493] Done running local_init_op.


[[128   3]
 [  3  17]]
              precision    recall  f1-score   support

           0       0.98      0.98      0.98       131
           1       0.85      0.85      0.85        20

   micro avg       0.96      0.96      0.96       151
   macro avg       0.91      0.91      0.91       151
weighted avg       0.96      0.96      0.96       151

F1 score:  0.9135496183206107


In [358]:
from outcomes_modelling import outcomes_sentence_labeler_plus_NER
outcomes_sentence_labeler_plus_NER = reload(outcomes_sentence_labeler_plus_NER)

_outcomes_sentence_labeler_plus_NER = outcomes_sentence_labeler_plus_NER.OutcomesSentenceLabelerPlusNer(
    "outcomes_new_%s_1"%label_to_train, path_to_NER="entity-recognition-model-more-1664", gpu_device_num=0)

Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done


In [342]:
train_data_df = _outcomes_sentence_labeler_plus_NER.prepare_df_data_sentences(outcomes_sentences_train_data, label_to_train, include_empty_sentences=True)
test_data_df = _outcomes_sentence_labeler_plus_NER.prepare_df_data_sentences(outcomes_sentences_eval_data, label_to_train, include_empty_sentences=True)

In [359]:
res = _outcomes_sentence_labeler_plus_NER.evaluate_model(test_data_df)

Used for model gpu 1
[[130   1]
 [  8  12]]
              precision    recall  f1-score   support

           0       0.94      0.99      0.97       131
           1       0.92      0.60      0.73        20

   micro avg       0.94      0.94      0.94       151
   macro avg       0.93      0.80      0.85       151
weighted avg       0.94      0.94      0.93       151

F1 score:  0.8469077391010478


In [240]:
for i in range(len(test_vals)):
    if test["label"].values[i] != res[i]:
        print(test_vals[i], res[i])

['reduce transportation costs' 1] 0
['improving global quality of life' 1] 0
['positive impact can be found in resource-rich populations' 1] 0
['reduce agricultural and pastoral risks' 1] 0
['female farmers may also benefit from such services' 0] 1
['Standardize and improve benefit coupling mechanism' 1] 0
[' Cultivate leading enterprise' 1] 0
[' Enhance farmer organization degree' 1] 0


In [334]:
for i in range(len(train_data_df)):
    if "risk" in train_data_df["text"].values[i]:
        print(train_data_df["text"].values[i], train_data_df["label"].values[i])

adapt their crop portfolio, moving away from low-risk, low-value crops toward more commercially oriented commodities 0
reduce the risk of investing 1
increasing risks of experiencing growth slowdowns and diminishing chances of experiencing growth accelerations 0
reduce their risks and transaction costs of accessing these services 0
a higher risk from pesticide exposure 0
have higher risks from increased pesticide exposure 0
lower risks of family/country conflicts, improvement in political stability and quality of life 0
reduces the risk of fertilizer losses 0
Understanding the influence of gender on risk exposure 0
better manage their consumption and their business risk 1
increase flood risk 0
imply an exposed risk to nutrition-related disease and potential food insecurity 0
increased risk of food-borne infectious diseases 0
build awareness and reduce risk 0
increasing the risk of the small farmer 1
marginalised farmers perceived extreme rainfall as riskier 0


In [208]:
pred_sentences = [
    ("improve livelihood", ),
    ("maximize farmer welfare",),
    ("maximize welfare",),
    ("reduce income",),
    ("reduce GHG",),
    ("increase productivity",)
]

In [317]:
predictions = _outcomes_extracted_labeler.predict_for_df(pd.DataFrame(pred_sentences, columns=["text"]))

INFO:tensorflow:Writing example 0 of 6


I1106 14:38:42.553262 139697590273856 base_bert_model.py:424] Writing example 0 of 6


INFO:tensorflow:*** Example ***


I1106 14:38:42.556041 139697590273856 base_bert_model.py:400] *** Example ***


INFO:tensorflow:guid: 


...

I1106 14:38:45.277765 139697590273856 saver.py:1270] Restoring parameters from outcomes_new_Livelihood_1/model.ckpt-94


INFO:tensorflow:Running local_init_op.


I1106 14:38:45.848966 139697590273856 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I1106 14:38:45.915914 139697590273856 session_manager.py:493] Done running local_init_op.


In [319]:
for i in range(len(pred_sentences)):
    print(pred_sentences[i], predictions[0][i], predictions[1][i])

('improve livelihood',) [0.0280929 0.9719071] 1
('maximize farmer welfare',) [0.03571642 0.96428365] 1
('maximize welfare',) [0.0344816  0.96551836] 1
('reduce income',) [0.02902093 0.9709791 ] 1
('reduce GHG',) [0.9946977  0.00530234] 0
('increase productivity',) [0.9952474  0.00475256] 0


In [5]:
from sklearn.metrics import f1_score
from text_processing import text_normalizer

def get_f1_score_test_data(test_data, intervention_labeler):
    res_pred, res_prob = intervention_labeler.predict_class(test_data.values, return_probs=True)
    res_true = test_data["Label"].values
    return f1_score(res_true, res_pred, average="macro")

def get_f1_multi_label(test_labels, y_true):
    test_labels = np.concatenate([np.asarray(labels)[:, np.newaxis] for labels in test_labels], axis=1)
    final_res = []
    for i in range(test_labels.shape[0]):
        identified_labels = set()
        for j in range(test_labels.shape[1]):
            if test_labels[i][j] >= 0.5:
                identified_labels.add(j+1)
        if not identified_labels:
            identified_labels.add(12)
        final_res.append(identified_labels)
    cnt = 0
    cnt_precision = 0
    cnt_recall = 0
    cnt_f1 = 0
    cnt_all_found = 0
    for idx, res in enumerate(y_true):
        cnt += 1
        cnt_intersect = len(y_true[idx].intersection(final_res[idx]))
        cnt_correct = len(y_true[idx])
        cnt_found = len(final_res[idx])
        precision = 0 if cnt_found == 0 else (cnt_intersect/cnt_found)
        recall = 0 if cnt_correct == 0 else (cnt_intersect/cnt_correct)
        f1 = 0
        if (precision + recall) > 0:
            f1 = 2*precision*recall/(precision + recall)
        cnt_precision += precision
        cnt_recall += recall
        if recall > 0.99:
            cnt_all_found += 1
        cnt_f1 += f1
    return cnt_f1/cnt

def get_f1_multi_label_new(test_labels, y_true):
    final_res = []
    for i in range(len(test_labels)):
        identified_labels = set()
        for j in range(len(test_labels[i])):
            if test_labels[i][j] >= 0.5:
                identified_labels.add(j+1)
        if not identified_labels:
            identified_labels.add(12)
        final_res.append(identified_labels)
    cnt = 0
    cnt_precision = 0
    cnt_recall = 0
    cnt_f1 = 0
    cnt_all_found = 0
    for idx, res in enumerate(y_true):
        cnt += 1
        cnt_intersect = len(y_true[idx].intersection(final_res[idx]))
        cnt_correct = len(y_true[idx])
        cnt_found = len(final_res[idx])
        precision = 0 if cnt_found == 0 else (cnt_intersect/cnt_found)
        recall = 0 if cnt_correct == 0 else (cnt_intersect/cnt_correct)
        f1 = 0
        if (precision + recall) > 0:
            f1 = 2*precision*recall/(precision + recall)
        cnt_precision += precision
        cnt_recall += recall
        if recall > 0.99:
            cnt_all_found += 1
        cnt_f1 += f1
    return cnt_f1/cnt

def get_accuracy_multi_label(test_labels, y_true):
    test_labels = np.concatenate([np.asarray(labels)[:, np.newaxis] for labels in test_labels], axis=1)
    final_res = []
    for i in range(test_labels.shape[0]):
        identified_labels = set()
        for j in range(test_labels.shape[1]):
            if test_labels[i][j] >= 0.5:
                identified_labels.add(j+1)
        if not identified_labels:
            identified_labels.add(12)
        final_res.append(identified_labels)
    cnt = 0
    cnt_precision = 0
    cnt_recall = 0
    cnt_f1 = 0
    cnt_all_found = 0
    for idx, res in enumerate(y_true):
        cnt += 1
        cnt_intersect = len(y_true[idx].intersection(final_res[idx]))
        cnt_correct = len(y_true[idx])
        cnt_found = len(final_res[idx])
        precision = 0 if cnt_found == 0 else (1 if cnt_intersect > 0 else 0)
        recall = 0 if cnt_correct == 0 else (1 if cnt_intersect > 0 else 0)
        f1 = 0
        if (precision + recall) > 0:
            f1 = 2*precision*recall/(precision + recall)
        cnt_precision += precision
        cnt_recall += recall
        if recall > 0.99:
            cnt_all_found += 1
        cnt_f1 += f1
    return cnt_f1/cnt

def get_accuracy_multi_label_new(test_labels, y_true):
    final_res = []
    for i in range(len(test_labels)):
        identified_labels = set()
        for j in range(len(test_labels[i])):
            if test_labels[i][j] >= 0.5:
                identified_labels.add(j+1)
        if not identified_labels:
            identified_labels.add(12)
        final_res.append(identified_labels)
    cnt = 0
    cnt_precision = 0
    cnt_recall = 0
    cnt_f1 = 0
    cnt_all_found = 0
    for idx, res in enumerate(y_true):
        cnt += 1
        cnt_intersect = len(y_true[idx].intersection(final_res[idx]))
        cnt_correct = len(y_true[idx])
        cnt_found = len(final_res[idx])
        precision = 0 if cnt_found == 0 else (1 if cnt_intersect > 0 else 0)
        recall = 0 if cnt_correct == 0 else (1 if cnt_intersect > 0 else 0)
        f1 = 0
        if (precision + recall) > 0:
            f1 = 2*precision*recall/(precision + recall)
        cnt_precision += precision
        cnt_recall += recall
        if recall > 0.99:
            cnt_all_found += 1
        cnt_f1 += f1
    return cnt_f1/cnt

def normalize_full(text):
    return " ".join(sorted(text_normalizer.normalize_sentence(text).split(" ")))

def deduplicate(dfs):
    dicts = {}
    for df in dfs:
        for i in range(len(df)):
            processed = normalize_full(df["Narrow concept"].values[i])
            if processed not in dicts:
                dicts[processed] = set()
            dicts[processed].add(df["Label"].values[i])
    return dicts

In [6]:
train_df = excel_reader.ExcelReader().read_folder("../tmp/usaid_water")
len(train_df)

Read file ../tmp/usaid_water/train_data.xlsx: 0.06s
Processed file ../tmp/usaid_water/train_data.xlsx: 0.03s
Read file ../tmp/usaid_water/labeled_sample_USAID.xlsx: 0.01s
Processed file ../tmp/usaid_water/labeled_sample_USAID.xlsx: 0.00s
Read file ../tmp/usaid_water/PA00JQVN_labeled_non_intervention.xlsx: 0.00s
Processed file ../tmp/usaid_water/PA00JQVN_labeled_non_intervention.xlsx: 0.00s
Read file ../tmp/usaid_water/part_sentences_model_check_Jaron.xlsx: 0.01s
Processed file ../tmp/usaid_water/part_sentences_model_check_Jaron.xlsx: 0.00s
Read file ../tmp/usaid_water/interv_from_sentences.xlsx: 0.19s
Processed file ../tmp/usaid_water/interv_from_sentences.xlsx: 0.10s
Read file ../tmp/usaid_water/data_sample_to_label_JP.xlsx: 0.01s
Processed file ../tmp/usaid_water/data_sample_to_label_JP.xlsx: 0.00s
Read file ../tmp/usaid_water/additionally_labelled_low_prob.xlsx: 0.01s
Processed file ../tmp/usaid_water/additionally_labelled_low_prob.xlsx: 0.00s


8597

In [7]:
from interventions_labeling_lib import usaid_intervention_labels
train_df["Label"] = [usaid_intervention_labels.USAIDInterventionLabels.INTERVENTION_LABEL_TO_NUMBER[train_df["Label"].values[i]] for i in range(len(train_df))]
deduplicated2labels = deduplicate([train_df])
train_df["Label"].value_counts()

1     1201
11    1186
2     1097
10    1006
8      987
7      831
5      575
12     515
9      515
6      486
4      129
3       69
Name: Label, dtype: int64

In [8]:
from sklearn.model_selection import train_test_split
x_train_ind, x_test_ind, y_train, y_test = train_test_split(
            train_df.drop("Label", axis=1), train_df["Label"].values,
            test_size=0.1, random_state=1237, stratify=train_df["Label"].values)
train_data = pd.concat([x_train_ind.reset_index(drop=True), pd.DataFrame({"Label": y_train})], axis=1)
test_data = pd.concat([x_test_ind.reset_index(drop=True), pd.DataFrame({"Label": y_test})], axis=1)

In [14]:
from bert_models import base_bert_model_interventions

common_folder = "/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi"
test_labels = []
for label in usaid_intervention_labels.USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL:
    if label != 10:
        print("#### ", usaid_intervention_labels.USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[label])
        train_copy = train_data.copy()
        test_copy = test_data.copy()
        train_copy["Label"] = [1 if label in deduplicated2labels[normalize_full(train_copy["Narrow concept"].values[i])] else 0 for i in range(len(train_copy))]
        test_copy["Label"] = [1 if label in deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] else 0 for i in range(len(test_copy))]
        
        _intervention_labeler = base_bert_model_interventions.BaseBertModelInterventions(
            os.path.join(common_folder, usaid_intervention_labels.USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[label]),
            [0,1], label_column="Label"
        )
        _intervention_labeler.train_model(train_copy, test_copy)
        
        res_prob, res_label, _ = _intervention_labeler.predict_for_df(test_copy)
        test_labels.append([r[1] for r in res_prob])

print("F1 measure: ", get_f1_multi_label(test_labels, [deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] for i in range(len(test_data))]))
print("Accuracy: ",get_accuracy_multi_label(test_labels, [deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] for i in range(len(test_data))]))

####  Water infrastructure
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
1449
Beginning Training!
Training took time  0:00:00.006161
Used for model gpu 1
[[692  15]
 [ 17 136]]
              precision    recall  f1-score   support

           0       0.98      0.98      0.98       707
           1       0.90      0.89      0.89       153

   micro avg       0.96      0.96      0.96       860
   macro avg       0.94      0.93      0.94       860
weighted avg       0.96      0.96      0.96       860

F1 score:  0.9360689860243829
Used for model gpu 1
####  Sanitation/Hygiene
Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
1449
Beginning Training!
Used for model gpu 1
Used for model gpu 1
Training took time  0:09:30.703767
Used for model gpu 1
[[696   6]
 [ 17 141]]
              precision    recall  f1-score   support

           0       0.98      0.99      0.98       702
           1       0.96    

In [20]:
from bert_models import base_bert_model
base_bert_model = reload(base_bert_model)
from bert_models import base_bert_model_interventions
base_bert_model_interventions = reload(base_bert_model_interventions)

common_folder = "/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_1"
_intervention_labeler = base_bert_model_interventions.BaseBertModelInterventions(
    common_folder,
    [0 for i in range(9)], label_column="label",
    multilabel=True
)

def prepare_labelled_data(train_data):
    train_copy = train_data.copy()
    train_copy["label"] = ""
    for i in range(len(train_copy)):
        real_labels = deduplicated2labels[normalize_full(train_copy["Narrow concept"].values[i])]
        real_labels_idx = []
        for idx in range(1, 10):
            real_labels_idx.append(int(idx in real_labels))
        train_copy["label"].values[i] = real_labels_idx
    return train_copy

train_copy = prepare_labelled_data(train_data)
test_copy = prepare_labelled_data(test_data)

_intervention_labeler.train_model(train_copy, test_copy)

res_prob, res_label, _ = _intervention_labeler.predict_for_df(test_copy)

print("F1 measure: ", get_f1_multi_label_new(res_prob, [deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] for i in range(len(test_data))]))
print("Accuracy: ",get_accuracy_multi_label_new(res_prob, [deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] for i in range(len(test_data))]))

Started tokenizer loading
Used gpu 0
INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I0213 20:19:37.179166 139899362359104 saver.py:1483] Saver not created because there are no variables in the graph to restore


Model partly loaded
Tokenizrer loaded
0
INFO:tensorflow:Using config: {'_model_dir': '/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_1', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f3bdda9f518>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


I0213 20:19:37.528754 139899362359104 estimator.py:201] Using config: {'_model_dir': '/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_1', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f3bdda9f518>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Config is done
INFO:tensorflow:Writing example 0 of 7733


...

INFO:tensorflow:Running local_init_op.


I0213 20:19:42.330813 139899362359104 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0213 20:19:42.401420 139899362359104 session_manager.py:493] Done running local_init_op.


F1 measure:  0.8425193798449607
Accuracy:  0.8732558139534884


In [9]:
from bert_models import base_bert_model
base_bert_model = reload(base_bert_model)
from bert_models import base_bert_model_interventions
base_bert_model_interventions = reload(base_bert_model_interventions)

common_folder = "/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_2"
_intervention_labeler = base_bert_model_interventions.BaseBertModelInterventions(
    common_folder,
    [0 for i in range(11)], label_column="label",
    multilabel=True
)

def prepare_labelled_data(train_data):
    train_copy = train_data.copy()
    train_copy["label"] = ""
    for i in range(len(train_copy)):
        real_labels = deduplicated2labels[normalize_full(train_copy["Narrow concept"].values[i])]
        real_labels_idx = []
        for idx in range(1, 12):
            real_labels_idx.append(int(idx in real_labels))
        train_copy["label"].values[i] = real_labels_idx
    return train_copy

train_copy = prepare_labelled_data(train_data)
test_copy = prepare_labelled_data(test_data)

_intervention_labeler.train_model(train_copy, test_copy)

res_prob, res_label, _ = _intervention_labeler.predict_for_df(test_copy)

print("F1 measure: ", get_f1_multi_label_new(res_prob, [deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] for i in range(len(test_data))]))
print("Accuracy: ",get_accuracy_multi_label_new(res_prob, [deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[i])] for i in range(len(test_data))]))

Started tokenizer loading
Used gpu 0
Instructions for updating:
Colocations handled automatically by placer.


W0303 16:39:53.724453 140273998071616 deprecation.py:323] From /home/maryia_pavlovets/.conda/envs/maryia_pavlovets_env/lib/python3.7/site-packages/tensorflow/python/ops/control_flow_ops.py:3632: colocate_with (from tensorflow.python.framework.ops) is deprecated and will be removed in a future version.
Instructions for updating:
Colocations handled automatically by placer.


INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I0303 16:39:55.072811 140273998071616 saver.py:1483] Saver not created because there are no variables in the graph to restore


Model partly loaded
Tokenizrer loaded
0
INFO:tensorflow:Using config: {'_model_dir': '/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_2', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f93380df898>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


...

INFO:tensorflow:Running local_init_op.


I0303 16:49:41.575302 140273998071616 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0303 16:49:41.642377 140273998071616 session_manager.py:493] Done running local_init_op.


F1 measure:  0.815426356589147
Accuracy:  0.8511627906976744


In [16]:
from bert_models import base_bert_model
base_bert_model = reload(base_bert_model)
from bert_models import base_bert_model_interventions
base_bert_model_interventions = reload(base_bert_model_interventions)

from sklearn.utils import shuffle

common_folder = "/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3"
_intervention_labeler = base_bert_model_interventions.BaseBertModelInterventions(
    common_folder,
    [0 for i in range(11)], label_column="label",
    multilabel=True
)

def prepare_labelled_data(train_data):
    train_copy = train_data.copy()
    train_copy["label"] = ""
    for i in range(len(train_copy)):
        real_labels = deduplicated2labels[normalize_full(train_copy["Narrow concept"].values[i])]
        real_labels_idx = []
        for idx in range(1, 12):
            real_labels_idx.append(int(idx in real_labels))
        train_copy["label"].values[i] = real_labels_idx
    return train_copy

train_copy_df = prepare_labelled_data(train_df)
train_copy_df = shuffle(train_copy_df)

_intervention_labeler.train_model(train_copy_df, [])

Started tokenizer loading
Used gpu 0
INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I0303 16:58:02.063705 140273998071616 saver.py:1483] Saver not created because there are no variables in the graph to restore


Model partly loaded
Tokenizrer loaded
0
INFO:tensorflow:Using config: {'_model_dir': '/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f93080d0e48>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


I0303 16:58:02.454256 140273998071616 estimator.py:201] Using config: {'_model_dir': '/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 500, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f93080d0e48>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Config is done
INFO:tensorflow:Writing example 0 of 8597


...

INFO:tensorflow:Saving checkpoints for 1611 into /hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3/model.ckpt.


I0303 17:08:35.572641 140273998071616 basic_session_run_hooks.py:594] Saving checkpoints for 1611 into /hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3/model.ckpt.


INFO:tensorflow:Loss for final step: 0.032665957.


I0303 17:08:37.428550 140273998071616 estimator.py:359] Loss for final step: 0.032665957.


Training took time  0:10:33.667194


In [17]:
res = _intervention_labeler.predict_for_df(pd.DataFrame(["faeces management", "fecal sludge management",
                                                        "disposal of feces", "faeces disposal",
                                                        "menstrual and fecal management"], columns=["text"]))

INFO:tensorflow:Writing example 0 of 5


I0303 17:10:49.847390 140273998071616 base_bert_model.py:478] Writing example 0 of 5


INFO:tensorflow:*** Example ***


I0303 17:10:49.849696 140273998071616 base_bert_model.py:454] *** Example ***


INFO:tensorflow:guid: 


...

I0303 17:10:52.626985 140273998071616 saver.py:1270] Restoring parameters from /hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3/model.ckpt-1611


INFO:tensorflow:Running local_init_op.


I0303 17:10:53.269925 140273998071616 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0303 17:10:53.336988 140273998071616 session_manager.py:493] Done running local_init_op.


In [10]:
from interventions_labeling_lib import usaid_intervention_labels
from sklearn.metrics import classification_report, confusion_matrix
for i in range(11):
    print(usaid_intervention_labels.USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[i+1])
    pred = []
    for j in range(len(test_copy)):
        if res_prob[j][i] >= 0.5:
            pred.append(1)
        else:
            pred.append(0)
    real_label = []
    for j in range(len(test_copy)):
        if (i+1) in deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[j])]:
            real_label.append(1)
        else:
            real_label.append(0)
    print(confusion_matrix(real_label,pred))
    print(classification_report(real_label,pred))

Water infrastructure
[[681  19]
 [ 27 133]]
              precision    recall  f1-score   support

           0       0.96      0.97      0.97       700
           1       0.88      0.83      0.85       160

   micro avg       0.95      0.95      0.95       860
   macro avg       0.92      0.90      0.91       860
weighted avg       0.95      0.95      0.95       860

Sanitation/Hygiene
[[724   5]
 [ 11 120]]
              precision    recall  f1-score   support

           0       0.99      0.99      0.99       729
           1       0.96      0.92      0.94       131

   micro avg       0.98      0.98      0.98       860
   macro avg       0.97      0.95      0.96       860
weighted avg       0.98      0.98      0.98       860

Fecal sludge management
[[852   0]
 [  6   2]]
              precision    recall  f1-score   support

           0       0.99      1.00      1.00       852
           1       1.00      0.25      0.40         8

   micro avg       0.99      0.99      0.99      

In [13]:
for j in range(len(test_copy)):
    if 3 in deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[j])]:
        print(test_copy["Narrow concept"].values[j], res_prob[j])

Fecal Sludge Management [0.03839445 0.10422119 0.54730266 0.18459827 0.18260509 0.13557991
 0.1123758  0.06305346 0.05250514 0.06351808 0.16914055]
monitoring for fecal indicator bacteria [0.03643382 0.09735352 0.41170263 0.20595396 0.43836117 0.24029815
 0.05105585 0.08080688 0.90769804 0.03098667 0.0675917 ]
faeces care [0.01235247 0.04291916 0.16378152 0.07731697 0.06385469 0.09786215
 0.04165897 0.08966142 0.01817471 0.01769477 0.17822203]
feces/menstrual management [0.06695381 0.0890308  0.26490396 0.80750036 0.14591327 0.14034548
 0.0426245  0.10938439 0.08584037 0.04511628 0.12629557]
analyzed for presence of fecal coliform [0.02951193 0.0460684  0.2090669  0.11116165 0.50014937 0.11590654
 0.03014296 0.05505002 0.83953553 0.017831   0.04008633]
handle and dispose of faeces and menstrual blood [0.07025996 0.11457908 0.28836143 0.8378805  0.18120393 0.13282639
 0.0577912  0.12578452 0.10147268 0.05185053 0.10950282]
Fecal Sludge Management [0.03839445 0.10422119 0.54730266 0.1845

In [18]:
from interventions_labeling_lib import usaid_intervention_labels
from sklearn.metrics import classification_report, confusion_matrix
for i in range(9):
    print(usaid_intervention_labels.USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[i+1])
    pred = []
    for j in range(len(test_copy)):
        if res_prob[j][i] >= 0.5:
            pred.append(1)
        else:
            pred.append(0)
    real_label = []
    for j in range(len(test_copy)):
        if (i+1) in deduplicated2labels[normalize_full(test_copy["Narrow concept"].values[j])]:
            real_label.append(1)
        else:
            real_label.append(0)
    print(confusion_matrix(real_label,pred))
    print(classification_report(real_label,pred))

Water infrastructure
[[694  13]
 [ 17 136]]
              precision    recall  f1-score   support

           0       0.98      0.98      0.98       707
           1       0.91      0.89      0.90       153

   micro avg       0.97      0.97      0.97       860
   macro avg       0.94      0.94      0.94       860
weighted avg       0.96      0.97      0.96       860

Sanitation/Hygiene
[[693   9]
 [ 12 146]]
              precision    recall  f1-score   support

           0       0.98      0.99      0.99       702
           1       0.94      0.92      0.93       158

   micro avg       0.98      0.98      0.98       860
   macro avg       0.96      0.96      0.96       860
weighted avg       0.98      0.98      0.98       860

Water quality
[[772  17]
 [ 14  57]]
              precision    recall  f1-score   support

           0       0.98      0.98      0.98       789
           1       0.77      0.80      0.79        71

   micro avg       0.96      0.96      0.96       860
   ma

In [4]:
from text_processing import abbreviations_resolver
abbreviations_resolver = reload(abbreviations_resolver)
filter_word_list = text_normalizer.build_filter_dictionary(["../data/Filter_Geo_Names.xlsx"])
_abbreviations_resolver = abbreviations_resolver.AbbreviationsResolver(filter_word_list)
_abbreviations_resolver.load_model("../model/abbreviations_dicts")

In [8]:
from interventions_labeling_lib.usaid_intervention_labels import USAIDInterventionLabels
from bert_models import base_bert_model
base_bert_model = reload(base_bert_model)
from bert_models import base_bert_model_interventions
base_bert_model_interventions = reload(base_bert_model_interventions)
from time import time
import spacy
from text_processing import abbreviations_resolver
abbreviations_resolver = reload(abbreviations_resolver)
import nltk

filter_word_list = text_normalizer.build_filter_dictionary(["../data/Filter_Geo_Names.xlsx"])
_abbreviations_resolver = abbreviations_resolver.AbbreviationsResolver(filter_word_list)
_abbreviations_resolver.load_model("../model/abbreviations_dicts")

common_folder = "/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3"
_intervention_labeler = base_bert_model_interventions.BaseBertModelInterventions(
    common_folder,
    [0 for i in range(11)], label_column="label",
    multilabel=True
)
ner_model = spacy.load("/hdd2/data/maryia_pavlovets/usaid_entity-recognition-model-more-3012-169_iter")
folder_to_save = "../tmp/check_metrics_new"
os.makedirs(folder_to_save, exist_ok=True)
cnt_processed = 0
folder_to_process = "../tmp/check_metrics"
for filename in os.listdir(folder_to_process):
    print(filename)
    try:
        start_time = time()
        filename_to_save = os.path.join(folder_to_save, filename)
        if os.path.exists(filename_to_save):
            cnt_processed += 1
            print("Already processed ", filename_to_save)
            continue
        df = excel_reader.ExcelReader().read_df_from_excel(os.path.join(folder_to_process, filename))
        found_data_all = []
        idx = 0
        idx2doc = {}
        for i in range(len(df)):
            text = df["Text"].values[i].replace("\n", " ")
            text = re.sub("[sencmaruotv]{15,1000}", " ", text).strip()
            for sentence in nltk.sent_tokenize(re.sub("\s+", " ", text)):
                found_data = []
                results = set()
                for res in ner_model(sentence).ents:
                    intervention = _abbreviations_resolver.replace_abbreviations(text=text_normalizer.normalize_sentence(
                        res.text)).strip()
                    intervnetion_words_set = set()
                    intervnetion_words = []
                    for w in intervention.split(" "):
                        if w not in intervnetion_words_set:
                            intervnetion_words_set.add(w)
                            intervnetion_words.append(w)
                    intervention = " ".join(intervnetion_words).strip()
                    if intervention:
                        found_data.append((intervention, intervention, sentence, res.text))
                        idx2doc[idx] = i
                        idx += 1
                found_data_all.extend(found_data)
        df_to_predict = pd.DataFrame(found_data_all, columns=["Narrow concept", "Broad concepts", "Sentence", "Raw intervention"])
        res_prob, res_label, _ = _intervention_labeler.predict_for_df(df_to_predict)
        all_data_found = []
        all_probs = []
        for i in range(len(found_data_all)):
            idx = idx2doc[i]
            identified_labels = set()
            identified_labels_probs = []
            for j in range(len(res_label[i])):
                if res_label[i][j] == 1:
                    identified_labels.add(USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[j+1])
                    identified_labels_probs.append((USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[j+1], res_prob[i][j]))
            if identified_labels:
                all_data_found.append((found_data_all[i][0], found_data_all[i][2], found_data_all[i][3],
                                       list(identified_labels), identified_labels_probs, df["Page"].values[idx], df["Filename"].values[idx]))
        new_df = pd.DataFrame(all_data_found, columns=["intervention", "sentence", "raw_intervention", "intervention_labels",
                                                       "intervention_thresholds", "page", "filename"])
        print("Processed time: %.2f s" % (time() - start_time))
        excel_writer.ExcelWriter().save_df_in_excel(new_df, filename_to_save)
        cnt_processed += 1
    except Exception as err:
        print(err)

Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
Sample_USAID_to_label_MR_02.11.21.xlsx
Read file ../tmp/check_metrics/Sample_USAID_to_label_MR_02.11.21.xlsx: 0.01s
Processed file ../tmp/check_metrics/Sample_USAID_to_label_MR_02.11.21.xlsx: 0.01s
Used for model gpu 1
Processed time: 26.00 s
Saving...
Saved to ../tmp/check_metrics_new/Sample_USAID_to_label_MR_02.11.21.xlsx


In [5]:
from interventions_labeling_lib.usaid_intervention_labels import USAIDInterventionLabels
from bert_models import base_bert_model
base_bert_model = reload(base_bert_model)
from bert_models import base_bert_model_interventions
base_bert_model_interventions = reload(base_bert_model_interventions)
from time import time
import spacy
from text_processing import abbreviations_resolver
abbreviations_resolver = reload(abbreviations_resolver)
import nltk

filter_word_list = text_normalizer.build_filter_dictionary(["../data/Filter_Geo_Names.xlsx"])
_abbreviations_resolver = abbreviations_resolver.AbbreviationsResolver(filter_word_list)
_abbreviations_resolver.load_model("../model/abbreviations_dicts")

common_folder = "../tmp/bert_usaid_interventions_multi_label_3"#"/hdd2/data/maryia_pavlovets/bert_usaid_interventions_multi_label_3"
_intervention_labeler = base_bert_model_interventions.BaseBertModelInterventions(
    common_folder,
    [0 for i in range(11)], label_column="label",
    multilabel=True
)
ner_model = spacy.load("../tmp/usaid_entity-recognition-model-more-3012-169_iter")

for folder_to_process, folder_to_save in [("../tmp/parsed_pdfs_bart", "../tmp/parsed_pdfs_bart_extracted"),
                                          ("../tmp/parsed_pdfs_longformer", "../tmp/parsed_pdfs_longformer_extracted")]:
    os.makedirs(folder_to_save, exist_ok=True)
    cnt_processed = 0
    for filename in os.listdir(folder_to_process):
        print(filename)
        try:
            start_time = time()
            filename_to_save = os.path.join(folder_to_save, filename)
            if os.path.exists(filename_to_save):
                cnt_processed += 1
                print("Already processed ", filename_to_save)
                continue
            df = excel_reader.ExcelReader().read_df_from_excel(os.path.join(folder_to_process, filename))
            found_data_all = []
            idx = 0
            idx2doc = {}
            for i in range(len(df)):
                text = df["summary"].values[i].replace("\n", " ")
                text = re.sub("[sencmaruotv]{15,1000}", " ", text).strip()
                for sentence in nltk.sent_tokenize(re.sub("\s+", " ", text)):
                    found_data = []
                    results = set()
                    for res in ner_model(sentence).ents:
                        intervention = _abbreviations_resolver.replace_abbreviations(text=text_normalizer.normalize_sentence(
                            res.text)).strip()
                        intervnetion_words_set = set()
                        intervnetion_words = []
                        for w in intervention.split(" "):
                            if w not in intervnetion_words_set:
                                intervnetion_words_set.add(w)
                                intervnetion_words.append(w)
                        intervention = " ".join(intervnetion_words).strip()
                        if intervention:
                            found_data.append((intervention, intervention, sentence, res.text))
                            idx2doc[idx] = i
                            idx += 1
                    found_data_all.extend(found_data)
            df_to_predict = pd.DataFrame(found_data_all, columns=["Narrow concept", "Broad concepts", "Sentence", "Raw intervention"])
            res_prob, res_label, _ = _intervention_labeler.predict_for_df(df_to_predict)
            all_data_found = []
            all_probs = []
            for i in range(len(found_data_all)):
                idx = idx2doc[i]
                identified_labels = set()
                identified_labels_probs = []
                for j in range(len(res_label[i])):
                    if res_label[i][j] == 1:
                        identified_labels.add(USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[j+1])
                        identified_labels_probs.append((USAIDInterventionLabels.INTERVENTION_NUMBER_TO_LABEL[j+1], res_prob[i][j]))
                if identified_labels:
                    all_data_found.append((found_data_all[i][0], found_data_all[i][2], found_data_all[i][3],
                                           list(identified_labels), identified_labels_probs, df["Page"].values[idx], df["Filename"].values[idx]))
            new_df = pd.DataFrame(all_data_found, columns=["intervention", "sentence", "raw_intervention", "intervention_labels",
                                                           "intervention_thresholds", "page", "filename"])
            print("Processed time: %.2f s" % (time() - start_time))
            excel_writer.ExcelWriter().save_df_in_excel(new_df, filename_to_save)
            cnt_processed += 1
        except Exception as err:
            print(err)

Started tokenizer loading
Used gpu 0
Model partly loaded
Tokenizrer loaded
0
Config is done
263-A-13-00004.xlsx
Read file ../tmp/parsed_pdfs_bart\263-A-13-00004.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\263-A-13-00004.xlsx: 0.00s
Used for model gpu 1
Processed time: 82.39 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\263-A-13-00004.xlsx
278-C-17-00002.xlsx
Already processed  ../tmp/parsed_pdfs_bart_extracted\278-C-17-00002.xlsx
656-A-00-09-00134-00.xlsx
Read file ../tmp/parsed_pdfs_bart\656-A-00-09-00134-00.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\656-A-00-09-00134-00.xlsx: 0.00s
Used for model gpu 1
Processed time: 48.79 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\656-A-00-09-00134-00.xlsx
669-A-00-09-00001-00.xlsx
Read file ../tmp/parsed_pdfs_bart\669-A-00-09-00001-00.xlsx: 0.04s
Processed file ../tmp/parsed_pdfs_bart\669-A-00-09-00001-00.xlsx: 0.01s
Used for model gpu 1
Processed time: 89.70 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracte

Used for model gpu 1
Processed time: 30.56 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\AID-492-H-15-00001_Second .xlsx
AID-497-C-11-00001.xlsx
Read file ../tmp/parsed_pdfs_bart\AID-497-C-11-00001.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\AID-497-C-11-00001.xlsx: 0.00s
Used for model gpu 1
Processed time: 59.51 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\AID-497-C-11-00001.xlsx
AID-497-C-16-00003.xlsx
Read file ../tmp/parsed_pdfs_bart\AID-497-C-16-00003.xlsx: 0.37s
Processed file ../tmp/parsed_pdfs_bart\AID-497-C-16-00003.xlsx: 0.09s
Used for model gpu 1
Processed time: 652.73 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\AID-497-C-16-00003.xlsx
AID-517-A-16-00001.xlsx
Read file ../tmp/parsed_pdfs_bart\AID-517-A-16-00001.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\AID-517-A-16-00001.xlsx: 0.00s
Used for model gpu 1
Processed time: 32.89 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\AID-517-A-16-00001.xlsx
AID-521-C-17-00002.xlsx
Re

Used for model gpu 1
Processed time: 23.81 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00HP7T.xlsx
PA00HQCQ.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00HQCQ.xlsx: 0.01s
Processed file ../tmp/parsed_pdfs_bart\PA00HQCQ.xlsx: 0.00s
Used for model gpu 1
Processed time: 22.45 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00HQCQ.xlsx
PA00HRT9.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00HRT9.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\PA00HRT9.xlsx: 0.00s
Used for model gpu 1
Processed time: 34.97 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00HRT9.xlsx
PA00HSQT.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00HSQT.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\PA00HSQT.xlsx: 0.00s
Used for model gpu 1
Processed time: 55.26 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00HSQT.xlsx
PA00HT3K.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00HT3K.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\PA00HT3K.xlsx: 0.01s
Used for model gpu 1
Processed time:

Used for model gpu 1
Processed time: 70.22 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JPRX.xlsx
PA00JQ65.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00JQ65.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\PA00JQ65.xlsx: 0.00s
Used for model gpu 1
Processed time: 87.61 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JQ65.xlsx
PA00JQ67.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00JQ67.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\PA00JQ67.xlsx: 0.00s
Used for model gpu 1
Processed time: 56.70 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JQ67.xlsx
PA00JQQS.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00JQQS.xlsx: 0.05s
Processed file ../tmp/parsed_pdfs_bart\PA00JQQS.xlsx: 0.01s
Used for model gpu 1
Processed time: 90.05 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JQQS.xlsx
PA00JQT3.xlsx
Already processed  ../tmp/parsed_pdfs_bart_extracted\PA00JQT3.xlsx
PA00JQT5.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00JQT5.xlsx: 0.02s
Processed file 

Used for model gpu 1
Processed time: 13.80 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JXNF.xlsx
PA00JZ5T.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00JZ5T.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_bart\PA00JZ5T.xlsx: 0.00s
Used for model gpu 1
Processed time: 24.57 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JZ5T.xlsx
PA00JZJT.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00JZJT.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_bart\PA00JZJT.xlsx: 0.01s
Used for model gpu 1
Processed time: 97.84 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00JZJT.xlsx
PA00JZQV.xlsx
Already processed  ../tmp/parsed_pdfs_bart_extracted\PA00JZQV.xlsx
PA00K3ZF.xlsx
Already processed  ../tmp/parsed_pdfs_bart_extracted\PA00K3ZF.xlsx
PA00K48R.xlsx
Read file ../tmp/parsed_pdfs_bart\PA00K48R.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_bart\PA00K48R.xlsx: 0.01s
Used for model gpu 1
Processed time: 98.21 s
Saving...
Saved to ../tmp/parsed_pdfs_bart_extracted\PA00K48R.xlsx
PA0

...

Used for model gpu 1
Processed time: 72.93 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACN883.xlsx
PDACO418.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDACO418.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_longformer\PDACO418.xlsx: 0.00s
Used for model gpu 1
Processed time: 34.10 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACO418.xlsx
PDACP437.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDACP437.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_longformer\PDACP437.xlsx: 0.00s
Used for model gpu 1
Processed time: 57.66 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACP437.xlsx
PDACP464.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDACP464.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_longformer\PDACP464.xlsx: 0.00s
Used for model gpu 1
Processed time: 29.02 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACP464.xlsx
PDACP847.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDACP847.xlsx: 0.01s
Processed file ../tmp/parsed_p

Used for model gpu 1
Processed time: 136.19 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACY281.xlsx
PDACY292.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDACY292.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_longformer\PDACY292.xlsx: 0.00s
Used for model gpu 1
Processed time: 34.92 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACY292.xlsx
PDACY321.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDACY321.xlsx: 0.09s
Processed file ../tmp/parsed_pdfs_longformer\PDACY321.xlsx: 0.02s
Used for model gpu 1
Processed time: 372.66 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDACY321.xlsx
PDBAN295.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDBAN295.xlsx: 0.04s
Processed file ../tmp/parsed_pdfs_longformer\PDBAN295.xlsx: 0.01s
Used for model gpu 1
Processed time: 97.17 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PDBAN295.xlsx
PDBBD487.xlsx
Read file ../tmp/parsed_pdfs_longformer\PDBBD487.xlsx: 0.01s
Processed file ../tmp/parsed

Processed time: 10.32 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAR444.xlsx
PNAAU179.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAU179.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_longformer\PNAAU179.xlsx: 0.00s
Used for model gpu 1
Processed time: 38.34 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAU179.xlsx
PNAAU412.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAU412.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_longformer\PNAAU412.xlsx: 0.00s
Used for model gpu 1
Processed time: 70.06 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAU412.xlsx
PNAAU624.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAU624.xlsx: 0.08s
Processed file ../tmp/parsed_pdfs_longformer\PNAAU624.xlsx: 0.03s
Used for model gpu 1
Processed time: 221.42 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAU624.xlsx
PNAAV182.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAV182.xlsx: 0.01s
Processed file ../tmp/parsed_pdfs_longformer\PNAAV

Used for model gpu 1
Processed time: 46.30 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAZ351.xlsx
PNAAZ352.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAZ352.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_longformer\PNAAZ352.xlsx: 0.00s
Used for model gpu 1
Processed time: 114.70 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAZ352.xlsx
PNAAZ353.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAZ353.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_longformer\PNAAZ353.xlsx: 0.00s
Used for model gpu 1
Processed time: 9.08 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAZ353.xlsx
PNAAZ556.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAZ556.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_longformer\PNAAZ556.xlsx: 0.01s
Used for model gpu 1
Processed time: 48.79 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNAAZ556.xlsx
PNAAZ980.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNAAZ980.xlsx: 0.07s
Processed file ../tmp/parsed_p

Used for model gpu 1
Processed time: 39.21 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNABS812.xlsx
PNADP825.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNADP825.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_longformer\PNADP825.xlsx: 0.01s
Used for model gpu 1
Processed time: 144.68 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNADP825.xlsx
PNADR651.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNADR651.xlsx: 0.03s
Processed file ../tmp/parsed_pdfs_longformer\PNADR651.xlsx: 0.01s
Used for model gpu 1
Processed time: 101.62 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNADR651.xlsx
PNADR652.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNADR652.xlsx: 0.02s
Processed file ../tmp/parsed_pdfs_longformer\PNADR652.xlsx: 0.00s
Used for model gpu 1
Processed time: 104.82 s
Saving...
Saved to ../tmp/parsed_pdfs_longformer_extracted\PNADR652.xlsx
PNADR653.xlsx
Read file ../tmp/parsed_pdfs_longformer\PNADR653.xlsx: 0.02s
Processed file ../tmp/parse

# Measurements baseline

In [8]:
from nltk.stem.wordnet import WordNetLemmatizer
import spacy
import re

import sys
sys.path.append('../src')
from text_processing import text_normalizer

nlp = spacy.load('en_core_web_sm')
lmtzr = WordNetLemmatizer()

In [33]:
from utilities import excel_reader
articles_df = excel_reader.ExcelReader().read_distributed_df_from_excel('../notebooks/teams_dataset')
len(articles_df)

89944

In [29]:
def getPredictions(in_sentences):
  labels = ["Is not Measured", "Measured"]
  input_examples = [run_classifier.InputExample(guid="", text_a =x[0], text_b = x[1] + " " + x[2], label = 0) for x in in_sentences] # here, "" is just a dummy label
  input_features = run_classifier.convert_examples_to_features(input_examples, label_list, MAX_SEQ_LENGTH, tokenizer)
  predict_input_fn = run_classifier.input_fn_builder(features=input_features, seq_length=MAX_SEQ_LENGTH, is_training=False, drop_remainder=False)
  predictions = estimator.predict(predict_input_fn)
  return [prediction['labels'] for sentence, prediction in zip(in_sentences, predictions)]

In [35]:
import os
folder_to_save ="teams_dataset_interv_new"
#os.makedirs(folder_to_save)

In [17]:
def find_positions_of_words(text_words, marker_words_set):
    positions_found = {}
    for i in range(len(text_words)):
        for offset in range(5):
            text_to_check = " ".join(text_words[i:i+offset])
            if text_to_check in marker_words_set:
                positions_found[text_to_check] = i
    for word in marker_words_set:
        if word not in positions_found:
            positions_found[word] = 0
    return positions_found

def apply_only_closest_word_for_measurement(sent, num, measurements):
    res = []
    text_words = text_normalizer.get_stemmed_words_inverted_index(sent)
    words_to_check = [measure[0] for measure in measurements if measure[1] == 1] + [num]
    positions_found = find_positions_of_words(text_words, words_to_check)
    num_pos = positions_found[num]
    min_dist, word_min = 1000, ""
    for word in positions_found:
        if word != num:
            if abs(positions_found[word] - num_pos) < min_dist:
                min_dist, word_min = abs(positions_found[word] - num_pos), word
    for measure in measurements:
        res.append((measure[0], int(measure[0] == word_min), measure[2]))
    return res

In [18]:
def identify_measurements(pairs_to_check):
    dict_measure = {}
    for idx, pair in enumerate(pairs_to_check):
        if pair[0] not in dict_measure:
            dict_measure[pair[0]] = {}
        if pair[1] not in dict_measure[pair[0]]:
            dict_measure[pair[0]][pair[1]] = []
        dict_measure[pair[0]][pair[1]].append((pair[2],pair[3],idx))
    for sent in dict_measure:
        for num in dict_measure[sent]:
            if len(dict_measure[sent][num]) > 1:
                measures = apply_only_closest_word_for_measurement(sent, num, dict_measure[sent][num])
                dict_measure[sent][num] = measures
    new_dict = {}
    for sent in dict_measure:
        for num in dict_measure[sent]:
            for res in dict_measure[sent][num]:
                new_dict[res[-1]] = (sent, num, res[0],res[1])
    measurements = []
    for i in range(max(new_dict) +1):
        measurements.append(new_dict[i])
    return measurements

In [37]:
import nltk
import os
cnt_art_interv = {}
cnt_art_crop = {}
cnt_art_ids = set()
cnrt_art_ids_for_crops = set()
cnrt_art_all = {}
all_data = []
from time import time
import pickle
folder_to_save ="teams_dataset_interv_new"# "res_bert_all_dataset"

sentId2docId = {}
sentId = 0
pairsToProcess = []
time_start = time()
for docId in range(len(articles_df)):
    sentences = [articles_df["title_translated"].values[docId]]
    sentences.extend(nltk.sent_tokenize(articles_df["abstract_translated"].values[docId]))
    for sentence in sentences:
        for m in re.finditer(r"\b\d+[\w.,]*\d*\b", sentence):
            number = m.group(0)
            for intervention in articles_df["interventions_found_raw"].values[docId]:
                interv_set = set([intervention])#.union(search_engine_inverted_index.extend_query_with_abbreviations(intervention, extend_with_abbreviations = True))
                for interv in interv_set:
                    if interv in sentence:
                        sentId2docId[sentId] = ("interv", docId)
                        sentId += 1
                        pairsToProcess.append((sentence,number,interv))
            for crop in articles_df["plant_products_search"].values[docId]:
                for keyword in [crop]:#search_engine_inverted_index.find_similar_words_by_spelling(crop, 0.88):
                    if keyword in sentence:
                        sentId2docId[sentId] = ("crop", docId)
                        sentId += 1
                        pairsToProcess.append((sentence,number,keyword))
            for crop in articles_df["animal_products_search"].values[docId]:
                for keyword in [crop]:#search_engine_inverted_index.find_similar_words_by_spelling(crop, 0.88):
                    if keyword in sentence:
                        sentId2docId[sentId] = ("crop", docId)
                        sentId += 1
                        pairsToProcess.append((sentence,number,keyword))
    cnrt_art_all[docId] = [articles_df["interventions_found_raw"].values[docId], articles_df["plant_products_search"].values[docId],\
                          articles_df["animal_products_search"].values[docId]]
    if docId % 500 == 0 or docId == len(articles_df) -1:
        print("Processed %d articles" % docId)
        print("Processing ", time()-time_start)
        time_start = time()
    if (docId % 500 == 0 or docId == len(articles_df) -1) and len(pairsToProcess) != 0:
        if len(pairsToProcess) % 2 != 0:
            sentId2docId[sentId] = sentId2docId[sentId-1]
            sentId += 1
            pairsToProcess.append(pairsToProcess[-1])
        pred_vals = getPredictions(pairsToProcess)
        pairs_to_check = []
        for idx,pair in enumerate(pairsToProcess):
            pairs_to_check.append(tuple(list(pair) + [pred_vals[idx]]))
        all_data.extend(pairs_to_check)
        measurements = identify_measurements(pairs_to_check)
        print("Measurements were predicted")
        for i in range(len(measurements)):
            if sentId2docId[i][0] == "interv" and measurements[i][-1]:
                cnt_art_ids.add(sentId2docId[i][1])
                if sentId2docId[i][1] not in cnt_art_interv:
                    cnt_art_interv[sentId2docId[i][1]] = set()
                cnt_art_interv[sentId2docId[i][1]].add(pairsToProcess[i][2])
            if sentId2docId[i][0] == "crop" and measurements[i][-1]:
                cnrt_art_ids_for_crops.add(sentId2docId[i][1])
                if sentId2docId[i][1] not in cnt_art_crop:
                    cnt_art_crop[sentId2docId[i][1]] = set()
                cnt_art_crop[sentId2docId[i][1]].add(pairsToProcess[i][2])
        sentId2docId = {}
        sentId = 0
        pairsToProcess = []
        print("Predicting ", time()-time_start)
        time_start = time()
    if (docId % 3000 == 0 or docId == len(articles_df) -1):
        pickle.dump([cnt_art_interv, cnt_art_crop, cnt_art_ids, cnrt_art_ids_for_crops, cnrt_art_all, all_data],\
                    open(os.path.join(folder_to_save, "%d.pickle"%docId),"wb"))
        cnt_art_interv = {}
        cnt_art_crop = {}
        cnt_art_ids = set()
        cnrt_art_ids_for_crops = set()
        cnrt_art_all = {}
        all_data = []

Processed 0 articles
Processing  0.010553359985351562
Processed 500 articles
Processing  0.6842317581176758
INFO:tensorflow:Writing example 0 of 1868


I0610 16:21:33.734110 139736767817536 run_classifier.py:774] Writing example 0 of 1868


INFO:tensorflow:*** Example ***


I0610 16:21:33.737215 139736767817536 run_classifier.py:461] *** Example ***


INFO:tensorflow:guid: 


...

INFO:tensorflow:Running local_init_op.


I0610 17:34:11.244398 139736767817536 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0610 17:34:11.407946 139736767817536 session_manager.py:493] Done running local_init_op.


Measurements were predicted
Predicting  21.075867652893066


In [20]:
import os
import pickle

last_maxId = 0
folder = "teams_measures"
file_ids = sorted([int(filename.replace(".pickle","")) for filename in os.listdir(folder)])
sent_dict_with_res = {}
for filename_id in file_ids:
    filename = str(filename_id) + ".pickle"
    cnt_art_interv, cnt_art_crop, cnt_art_ids, cnrt_art_ids_for_crops,cnrt_all,pairs_to_process = pickle.load(open(os.path.join(folder,filename),"rb"))
    for pair in pairs_to_process:
        if pair[-1] == 1:
            if pair[0] not in sent_dict_with_res:
                sent_dict_with_res[pair[0]] = {}
            if pair[1] not in sent_dict_with_res[pair[0]]:
                sent_dict_with_res[pair[0]][pair[1]] = []
            sent_dict_with_res[pair[0]][pair[1]].append(pair[2])

In [22]:
cnt = 0
all_count = 0
for sent in sent_dict_with_res:
    for num in sent_dict_with_res[sent]:
        if len(sent_dict_with_res[sent][num]) > 1:
            cnt += 1
        all_count += len(sent_dict_with_res[sent][num])
cnt, all_count, cnt / all_count

(8985, 49657, 0.180941257023179)

In [47]:
def predict_sentence_measurements(sentence, number, word_exp):
    doc = nlp(sentence)
    for word in doc:
        if word.tag_ in "CD" and re.search("\d+",word.text) != None and word.text.strip() == number:
            root = [token for token in doc if token.text == word.text][0]
            has_noun_ancestor = False
            for root_anc in list(root.ancestors):
                if has_noun_ancestor and "VB" in root_anc.tag_:
                    continue
                if "NN" in root_anc.tag_ and len(root_anc.text) > 1:
                    has_noun_ancestor = True
                if root_anc.text not in text_normalizer.stopwords_all and lmtzr.lemmatize(root_anc.text) not in text_normalizer.stopwords_all:
                    new_word = ""
                    for descendant in root_anc.subtree:
                        new_word = new_word + " "+ descendant.text
                    new_word = new_word.strip()
                    if word_exp in new_word:
                        return 1
    return 0

In [247]:
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.metrics import f1_score

def predict_for_df(temp_df):
    pred_vals = [predict_sentence_measurements(temp_df["Sentence"].values[i], str(temp_df["Number"].values[i]), temp_df["Word Expression"].values[i]) for i in range(len(temp_df))]
    true_vals = [temp_df["Label"].values[i] for i in range(len(temp_df))]
    print(confusion_matrix(true_vals, pred_vals))
    print("F1 score: ",f1_score(pred_vals, true_vals, average="macro"))

In [59]:
predict_for_df(temp_df)

[[1139  876]
 [ 353  602]]
F1 score:  0.5722101683545011


In [273]:
def count_labels(temp_df):
    dict_true_vals = {}
    for val in temp_df["Label"].values:
        if val not in dict_true_vals:
            dict_true_vals[val] = 0
        dict_true_vals[val] += 1
    return dict_true_vals[0]/len(temp_df)

In [365]:
#train_d = getPrediction(temp_df.values)
test_d = getPrediction(test.values)

INFO:tensorflow:Writing example 0 of 184


I0415 10:34:20.722052 140529355110208 run_classifier.py:774] Writing example 0 of 184


INFO:tensorflow:*** Example ***


I0415 10:34:20.725250 140529355110208 run_classifier.py:461] *** Example ***


INFO:tensorflow:guid: 


...

I0415 10:34:25.590407 140529355110208 saver.py:1270] Restoring parameters from bert_results_13/model.ckpt-264


INFO:tensorflow:Running local_init_op.


I0415 10:34:26.689019 140529355110208 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0415 10:34:26.851442 140529355110208 session_manager.py:493] Done running local_init_op.


In [202]:
from utilities import excel_writer
predictions_evals = []
#for i in range(len(temp_df)):
#    predictions_evals.append((temp_df["Sentence"].values[i], temp_df["Number"].values[i], temp_df["Word Expression"].values[i], train_d[i][1][0], train_d[i][1][1],"Measured" if temp_df["Label"].values[i] == 1 else "Is not Measured", train_d[i][2]))
for i in range(len(test)):
    predictions_evals.append((test["Sentence"].values[i], test["Number"].values[i], test["Word Expression"].values[i], test_d[i][1][0], test_d[i][1][1], "Measured" if test["Label"].values[i] == 1 else "Is not Measured", test_d[i][2]))
row_df = pd.DataFrame(predictions_evals,columns = ["Sentence","Number","Word expression","Is not measured","Measured", "Label", "Predicted Label"])
excel_writer.ExcelWriter().save_df_in_excel(row_df,"res_test.xlsx", column_probabilities=["Is not measured","Measured"], column_outliers=[("Label","Measured"),("Predicted Label","Measured")])

Saving...
Saved to res_test.xlsx


In [382]:
test_df = pd.read_excel("..//measurements_test.xlsx")
len(test_df)

290

In [410]:
pred_vals = getPrediction([(test_df["Sentence"].values[i], str(test_df["Number"].values[i]), test_df["Word Expression"].values[i]) for i in range(len(test_df))])
pred_vals = [1 if d[-1] == "Measured" else 0 for d in pred_vals]
true_vals = [test_df["Label"].values[i] for i in range(len(test_df))]
print(confusion_matrix(true_vals, pred_vals))
print("F1 score: ",f1_score(pred_vals, true_vals, average="macro"))

INFO:tensorflow:Writing example 0 of 290


I0415 14:08:26.702253 140529355110208 run_classifier.py:774] Writing example 0 of 290


INFO:tensorflow:*** Example ***


I0415 14:08:26.703652 140529355110208 run_classifier.py:461] *** Example ***


INFO:tensorflow:guid: 


...

INFO:tensorflow:Running local_init_op.


I0415 14:08:31.106180 140529355110208 session_manager.py:491] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0415 14:08:31.214858 140529355110208 session_manager.py:493] Done running local_init_op.


[[138   9]
 [ 37 106]]
F1 score:  0.8394241417497232


In [412]:
for i in range(len(pred_vals)):
    if pred_vals[i] == 0 and true_vals[i] == 1:
        print(test_df.values[i])

['The susceptibility of seeds of six local (Banjara, Borno brown, Gwallam, Kanannado brown, Kanannado white and Saddam) and four improved (189KD-288, IT89KD-391, IT90K-82-2 and IT97K-499-35) cowpea cultivars that were commonly grown in north eastern Nigeria to infestation by the cowpea storage bruchid, Callosobruchus maculatus (F.) (Coleoptera: Bruchidae) was evaluated in the laboratory at 30AC-35AC and 60%-65% RH.'
 '60%-65' 'cowpea storage' 1]
['The susceptibility of seeds of six local (Banjara, Borno brown, Gwallam, Kanannado brown, Kanannado white and Saddam) and four improved (189KD-288, IT89KD-391, IT90K-82-2 and IT97K-499-35) cowpea cultivars that were commonly grown in north eastern Nigeria to infestation by the cowpea storage bruchid, Callosobruchus maculatus (F.) (Coleoptera: Bruchidae) was evaluated in the laboratory at 30AC-35AC and 60%-65% RH.'
 '30AC-35AC' 'cowpea storage' 1]
['The acid detergent fibre, acid detergent lignin and cellulose were increased by 43.69, 49.56 an

In [385]:
count_labels(test_df)

0.506896551724138